In [0]:
from pyspark.sql.types import *
import pandas as pd
from pyspark.sql.functions import *
from graphframes import *

from datetime import datetime
from pyspark.sql.functions import *
from pyspark.sql.types import DateType

In [0]:
tripdelaysFilePath = "/FileStore/tables/departuredelays.csv"
airportsnaFilePath = "/FileStore/tables/airport_codes_na.txt"
tripdelaysParquet  = "/FileStore/tables/landing/tripdelays"
airportsnaParquet  = "/FileStore/tables/landing/airportsna"

In [0]:
display(spark.read.option("delimiter", "\t").csv(airportsnaFilePath))

_c0 _c1 _c2 _c3 City State Country IATA Abbotsford BC Canada YXX Aberdeen SD USA ABR Abilene TX USA ABI Akron OH USA CAK Alamosa CO USA ALS Albany GA USA ABY Albany NY USA ALB Albuquerque NM USA ABQ Alexandria LA USA AEX Allentown PA USA ABE Alliance NE USA AIA Alpena MI USA APN Altoona PA USA AOO Amarillo TX USA AMA Anahim Lake BC Canada YAA Anchorage AK USA ANC Appleton WI USA ATW Arviat NWT Canada YEK Asheville NC USA AVL Aspen CO USA ASE Athens GA USA AHN Atlanta GA USA ATL Atlantic City NJ USA ACY Augusta GA USA AGS Augusta ME USA AUG Austin TX USA AUS Bagotville PQ Canada YBG Baie-Comeau PQ Canada YBC Bakersfield CA USA BFL Baltimore MD USA BWI Bangor ME USA BGR Bar Harbor ME USA BHB Barrow AK USA BRW Baton Rouge LA USA BTR Beaumont TX USA BPT Beckley WV USA BKW Bedford MA USA BED Bellingham WA USA BLI Bemidji MN USA BJI Bethel AK USA BET Bettles AK USA BTT Billings MT USA BIL Binghamton NY USA BGM Birmingham AL USA BHM Bismarck ND USA BIS Bloomington IL USA BMI Bloomington IN USA BMG Bluefield WV USA BLF Boise ID USA BOI Boston MA USA BOS Bozeman MT USA BZN Brookings SD USA BKX Brownsville TX USA BRO Brunswick GA USA BQK Buffalo NY USA BUF Burbank CA USA BUR Burlington IA USA BRL Burlington MA USA BBF Burlington VT USA BTV Butte MT USA BTM Calgary AB Canada YYC Campbell River BC Canada YBL Cap-aux-Meules, Magdalens Islands PQ Canada YGR Cape Girardeau MO USA CGI Carlsbad CA USA CLD Carlsbad NM USA CNM Casper WY USA CPR Castlegar BC Canada YCG Cedar Rapids IA USA CID Champaign IL USA CMI Charleston SC USA CHS Charleston WV USA CRW Charlotte NC USA CLT Charlottesville VA USA CHO Charlottetown PEI Canada YYG Chattanooga TN USA CHA Cheyenne WY USA CYS Chibougamau PQ Canada YMT Chicago IL USA MDW Chicago IL USA ORD Chicago IL USA CHI Chico CA USA CIC Churchill MB Canada YYQ Cincinnati OH USA CVG Clarksburg WV USA CKB Cleveland OH USA CLE Clovis NM USA CVN Cody WY USA COD College Station TX USA CLL Colorado Springs CO USA COS Columbia MO USA COU Columbia SC USA CAE Columbus GA USA CSG Columbus IN USA CLU Columbus MS USA GTR Columbus NE USA OLU Columbus OH USA CMH Cordova AK USA CDV Corpus Christi TX USA CRP Cranbrook BC Canada YXC Dallas TX USA DFW Dallas TX USA DAL Dayton OH USA DAY Daytona Beach FL USA DAB Decatur IL USA DEC Deer Lake NF Canada YDF Denver CO USA DEN Des Moines IA USA DSM Detroit MI USA DTW Detroit MI USA DTT Devils Lake ND USA DVL Dickinson ND USA DIK Dillingham AK USA DLG Dodge City KS USA DDC Dothan AL USA DHN Dryden ON Canada YHD Du Bois PA USA DUJ Dubuque IA USA DBQ Duluth MN USA DLH Durango CO USA DRO Dutch Harbor, Un Island AK USA DUT Eau Claire WI USA EAU Edmonton AB Canada YEG Eek AK USA EEK El Centro CA USA IPL El Dorado AR USA ELD El Paso TX USA ELP Elko NV USA EKO Elmira NY USA ELM Enid OK USA WDG Erie PA USA ERI Escanaba MI USA ESC Eugene OR USA EUG Eureka CA USA ACV Evansville IN USA EVV Fairbanks AK USA FAI Fargo ND USA FAR Farmington NM USA FMN Fayetteville AR USA XNA Fayetteville NC USA FAY Flagstaff AZ USA FLG Flin Flon MB Canada YFO Flint MI USA FNT Florence SC USA FLO Fort Dodge IA USA FOD Fort Lauderdale FL USA FLL Fort Leonard Wood MO USA TBN Fort McMurray AB Canada YMM Fort Myers FL USA RSW Fort Nelson BC Canada YYE Fort Saint John BC Canada YXJ Fort Smith AR USA FSM Fort Smith NWT Canada YSM Fort Walton Beach FL USA VPS Fort Wayne IN USA FWA Fort Yukon AK USA FYU Fredericton NB Canada YFC Fresno CA USA FAT Gainesville FL USA GNV Gander NF Canada YQX Garden City KS USA GCK Gaspe PQ Canada YGP Gillette WY USA GCC Glendive MT USA GDV Grand Forks ND USA GFK Grand Island NE USA GRI Grand Junction CO USA GJT Grand Rapids MI USA GRR Grande Prairie AB Canada YQU Great Bend KS USA GBD Great Falls MT USA GTF Green Bay WI USA GRB Greenbrier WV USA LWB Greensboro NC USA GSO Greenville MS USA GLH Greenville NC USA PGV Greenville SC USA GSP Gulfport MS USA GPT Gunnison CO USA GUC Hagerstown MD USA HGR Halifax NS Canada YHZ Hamilton ON Canada YHM Hana, Maui HI USA HNM Hancock MI USA CMX Harlingen TX

In [0]:

# Read Airports data and create a temp table
spark.read.\
  option("header", "true").\
  option("inferschema", "true").\
  option("delimiter", "\t").\
  csv(airportsnaFilePath).\
  write.parquet(airportsnaParquet,mode='overwrite')
airportsna = spark.read.parquet(airportsnaParquet)
airportsna.createOrReplaceTempView("airports_na")

# Read departure Delays data and create a temp table
spark.read.\
  option("header", "true").\
  csv(tripdelaysFilePath).\
  write.parquet(tripdelaysParquet,mode='overwrite')
departureDelays = spark.read.parquet(tripdelaysParquet)
departureDelays.createOrReplaceTempView("departureDelays")

# Available IATA (International Air Transport Association) codes from the departuredelays sample dataset
tripIATA = spark.sql("select distinct iata from (select distinct origin as iata from departureDelays union all select distinct destination as iata from departureDelays) a")
tripIATA.createOrReplaceTempView("tripIATA")

# Only include airports with atleast one trip from the departureDelays dataset
airports = spark.sql("select f.IATA, f.City, f.State, f.Country from airports_na f join tripIATA t on t.IATA = f.IATA")
airports.createOrReplaceTempView("airports")

In [0]:
# Build `departureDelays_geo` DataFrame
# Obtain key attributes such as Date of flight, delays, distance, and airport information (Origin, Destination)  
departureDelays_geo = spark.sql("select cast(f.date as int) as tripid, cast(concat(concat(concat(concat(concat(concat('2014-', concat(concat(substr(cast(f.date as string), 1, 2), '-')), substr(cast(f.date as string), 3, 2)), ' '), substr(cast(f.date as string), 5, 2)), ':'), substr(cast(f.date as string), 7, 2)), ':00') as timestamp) as `localdate`, cast(f.delay as int), cast(f.distance as int), f.origin as src, f.destination as dst, o.city as city_src, d.city as city_dst, o.state as state_src, d.state as state_dst from departuredelays f join airports o on o.iata = f.origin join airports d on d.iata = f.destination") 

# RegisterTempTable
departureDelays_geo.createOrReplaceTempView("departureDelays_geo")

In [0]:
# Create Vertices (airports) and Edges (flights)
tripVertices = airports.withColumnRenamed("IATA", "id").distinct()
tripEdges = departureDelays_geo.select("tripid", "delay", "src", "dst", "city_dst", "state_dst")

In [0]:
# Build `tripGraph` GraphFrame
# This GraphFrame builds up on the vertices and edges based on our trips (flights)
tripGraph = GraphFrame(tripVertices, tripEdges)
print(tripGraph)

# Build `tripGraphPrime` GraphFrame
# This graphframe contains a smaller subset of data to make it easier to display motifs and subgraphs (below)
tripEdgesPrime = departureDelays_geo.select("tripid", "delay", "src", "dst")
tripGraphPrime = GraphFrame(tripVertices, tripEdgesPrime)

GraphFrame(v:[id: string, City: string ... 2 more fields], e:[src: string, dst: string ... 4 more fields])


In [0]:
print(f"Airports: {tripGraph.vertices.count()}")
print(f"Trips: {tripGraph.edges.count()}")

Airports: 279
Trips: 1361141


In [0]:
longestDelay = tripGraph.edges.groupBy().max("delay")
display(longestDelay)

max(delay) 1642

In [0]:
print(f'On-time / Early Flights: {tripGraph.edges.filter("delay <= 0").count()}')
print(f'Delayed Flights: {tripGraph.edges.filter("delay > 0").count()}')

On-time / Early Flights: 780469
Delayed Flights: 580672


In [0]:
# Delay can be <= 0 i.e. the flight left on time or early
sfoDelayedTrips = tripGraph.edges.\
  filter("src = 'SFO' and delay > 0").\
  groupBy("src", "dst").\
  avg("delay").\
  sort(desc("avg(delay)"))

In [0]:
display(sfoDelayedTrips)

src dst avg(delay) SFO OKC 59.073170731707314 SFO JAC 57.13333333333333 SFO COS 53.976190476190474 SFO OTH 48.09090909090909 SFO SAT 47.625 SFO MOD 46.80952380952381 SFO SUN 46.723404255319146 SFO CIC 46.72164948453608 SFO ABQ 44.8125 SFO ASE 44.285714285714285 SFO PIT 43.875 SFO MIA 43.81730769230769 SFO FAT 43.23972602739726 SFO MFR 43.11848341232228 SFO SBP 43.09770114942529 SFO MSP 42.766917293233085 SFO BOI 42.65482233502538 SFO RDM 41.98823529411764 SFO AUS 41.690677966101696 SFO SLC 41.407272727272726 SFO JFK 41.01379310344828 SFO PSP 40.909909909909906 SFO PHX 40.67272727272727 SFO MRY 40.61764705882353 SFO ACV 40.3728813559322 SFO LAS 40.107602339181284 SFO TUS 39.853658536585364 SFO SAN 38.97361809045226 SFO SBA 38.758620689655174 SFO BFL 38.51136363636363 SFO RDU 38.170731707317074 SFO STL 38.13513513513514 SFO IND 38.114285714285714 SFO EUG 37.573913043478264 SFO RNO 36.81372549019608 SFO BUR 36.75675675675676 SFO LGB 36.752941176470586 SFO HNL 36.25367647058823 SFO LAX 36.165543071161046 SFO RDD 36.11009174311926 SFO MSY 35.421052631578945 SFO SMF 34.936 SFO MDW 34.824742268041234 SFO FLL 34.76842105263158 SFO SEA 34.68854961832061 SFO MCI 34.68571428571428 SFO DFW 34.36642599277978 SFO OGG 34.171875 SFO PDX 34.14430894308943 SFO ORD 33.991130820399114 SFO LIH 32.93023255813954 SFO DEN 32.861491628614914 SFO PSC 32.604651162790695 SFO PHL 32.440677966101696 SFO BWI 31.70212765957447 SFO ONT 31.49079754601227 SFO SNA 31.18426103646833 SFO MCO 31.03488372093023 SFO MKE 31.03448275862069 SFO CLE 30.979591836734695 SFO EWR 30.354285714285716 SFO BOS 29.623471882640587 SFO LMT 29.233333333333334 SFO DTW 28.34722222222222 SFO IAH 28.322105263157894 SFO CVG 27.03125 SFO ATL 26.84860557768924 SFO IAD 26.125964010282775 SFO ANC 25.5 SFO BZN 23.964285714285715 SFO CLT 22.636363636363637 SFO DCA 21.896103896103895

In [0]:
# After displaying tripDelays, use Plot Options to set `state_dst` as a Key.
tripDelays = tripGraph.edges.filter("delay > 0")
display(tripDelays)

tripid delay src dst city_dst state_dst 1311815 43 MSY FLL Fort Lauderdale FL 1311545 29 MSY STL St. Louis MO 1311410 5 MSY BNA Nashville TN 1311545 15 MSY DAL Dallas TX 1311110 14 MSY EYW Key West FL 1310600 47 MSY DAL Dallas TX 1311835 38 MSY TPA Tampa FL 1311155 13 MSY LAS Las Vegas NV 1311910 56 MSY HOU Houston TX 1311310 6 MSY HOU Houston TX 1311655 15 MSY MCI Kansas City MO 1311220 41 MSY DAL Dallas TX 1311325 11 MSY FLL Fort Lauderdale FL 1311720 5 MSY BNA Nashville TN 1311440 3 MSY HOU Houston TX 1310810 1 MSY FLL Fort Lauderdale FL 1311250 6 MSY TPA Tampa FL 1311810 63 MSY DAL Dallas TX 1311640 11 MSY HOU Houston TX 1311720 27 MSY MCO Orlando FL 1311900 16 MSY MCO Orlando FL 1311100 3 MSY BNA Nashville TN 1311740 31 MSY DEN Denver CO 1311440 24 MSY DAL Dallas TX 1301750 20 MSY ATL Atlanta GA 1300745 58 MSY EWR Newark NJ 1301815 25 MSY FLL Fort Lauderdale FL 1301410 36 MSY BNA Nashville TN 1301215 19 MSY MCO Orlando FL 1301835 1 MSY TPA Tampa FL 1301155 10 MSY LAS Las Vegas NV 1301940 38 MSY DAL Dallas TX 1300940 11 MSY DAL Dallas TX 1301355 7 MSY BWI Baltimore MD 1301100 21 MSY HOU Houston TX 1301450 2 MSY LAX Los Angeles CA 1301005 1 MSY HOU Houston TX 1301220 30 MSY DAL Dallas TX 1301325 4 MSY FLL Fort Lauderdale FL 1301720 22 MSY BNA Nashville TN 1300725 2 MSY TPA Tampa FL 1300810 9 MSY FLL Fort Lauderdale FL 1301755 15 MSY HOU Houston TX 1301250 31 MSY TPA Tampa FL 1301810 139 MSY DAL Dallas TX 1301250 17 MSY PHX Phoenix AZ 1301610 4 MSY AUS Austin TX 1301640 57 MSY HOU Houston TX 1301720 32 MSY MCO Orlando FL 1301900 30 MSY MCO Orlando FL 1301100 5 MSY BNA Nashville TN 1301200 21 MSY HOU Houston TX 1300930 2 MSY MCO Orlando FL 1301440 20 MSY DAL Dallas TX 1291815 23 MSY FLL Fort Lauderdale FL 1291545 21 MSY STL St. Louis MO 1291410 11 MSY BNA Nashville TN 1291545 30 MSY DAL Dallas TX 1291835 18 MSY TPA Tampa FL 1291910 17 MSY HOU Houston TX 1291310 4 MSY HOU Houston TX 1291940 6 MSY DAL Dallas TX 1291355 14 MSY BWI Baltimore MD 1291450 20 MSY LAX Los Angeles CA 1291655 8 MSY MCI Kansas City MO 1291325 6 MSY FLL Fort Lauderdale FL 1291440 23 MSY HOU Houston TX 1291755 65 MSY HOU Houston TX 1291505 23 MSY MKE Milwaukee WI 1291250 15 MSY TPA Tampa FL 1291810 83 MSY DAL Dallas TX 1291640 25 MSY HOU Houston TX 1291500 56 MSY MDW Chicago IL 1291900 33 MSY MCO Orlando FL 1291740 23 MSY DEN Denver CO 1291440 23 MSY DAL Dallas TX 1280615 2 MSY DEN Denver CO 1280725 2 MSY TPA Tampa FL 1271750 11 MSY ATL Atlanta GA 1271815 19 MSY FLL Fort Lauderdale FL 1271545 19 MSY STL St. Louis MO 1271410 26 MSY BNA Nashville TN 1271215 7 MSY MCO Orlando FL 1271110 3 MSY EYW Key West FL 1271835 29 MSY TPA Tampa FL 1271155 5 MSY LAS Las Vegas NV 1271910 4 MSY HOU Houston TX 1270715 3 MSY BWI Baltimore MD 1271310 4 MSY HOU Houston TX 1270920 10 MSY STL St. Louis MO 1271940 22 MSY DAL Dallas TX 1270940 17 MSY DAL Dallas TX 1271355 6 MSY BWI Baltimore MD 1271100 15 MSY HOU Houston TX 1271450 5 MSY LAX Los Angeles CA 1271005 18 MSY HOU Houston TX 1271655 4 MSY MCI Kansas City MO 1271220 23 MSY DAL Dallas TX 1271630 4 MSY LAS Las Vegas NV 1271325 19 MSY FLL Fort Lauderdale FL 1270725 7 MSY TPA Tampa FL 1271440 10 MSY HOU Houston TX 1271755 14 MSY HOU Houston TX 1271505 19 MSY MKE Milwaukee WI 1271250 2 MSY TPA Tampa FL 1271810 17 MSY DAL Dallas TX 1271250 3 MSY PHX Phoenix AZ 1271640 7 MSY HOU Houston TX 1271720 12 MSY MCO Orlando FL 1270755 8 MSY BNA Nashville TN 1271130 17 MSY MDW Chicago IL 1271900 54 MSY MCO Orlando FL 1271100 19 MSY BNA Nashville TN 1271200 14 MSY HOU Houston TX 1271740 20 MSY DEN Denver CO 1270720 4 MSY HOU Houston TX 1270930 1 MSY MCO Orlando FL 1271440 27 MSY DAL Dallas TX 1261750 14 MSY ATL Atlanta GA 1261545 94 MSY DAL Dallas TX 1261110 52 MSY EYW Key West FL 1261835 5 MSY TPA Tampa FL 1261910 4 MSY HOU Houston TX 1261105 7 MSY BNA Nashville TN 1261450 1 MSY LAX Los Angeles CA 1261655 8 MSY MCI Kansas City MO 1261630 4 MSY LAS Las Vegas NV 1261755 4 MSY HOU Houston TX 1261640 3 MSY HOU Houston TX 1261800 3 MSY FLL Fo

In [0]:
display(tripGraph.degrees.sort(desc("degree")).limit(20))

id degree ATL 179774 DFW 133966 ORD 125405 LAX 106853 DEN 103699 IAH 85685 PHX 79672 SFO 77635 LAS 66101 CLT 56103 EWR 54407 MCO 54300 LGA 50927 SLC 50780 BOS 49936 DTW 46705 MSP 46235 SEA 45816 JFK 43661 BWI 42526

In [0]:
motifs = tripGraphPrime.\
  find("(a)-[ab]->(b); (b)-[bc]->(c)").\
  filter("(b.id = 'SFO') and (ab.delay > 500 or bc.delay > 500) and bc.tripid > ab.tripid and bc.tripid < ab.tripid + 10000")

display(motifs)

a ab b bc c List(MSY, New Orleans, LA, USA) List(1201725, 2, MSY, SFO) List(SFO, San Francisco, CA, USA) List(1211508, 593, SFO, JFK) List(JFK, New York, NY, USA) List(MSY, New Orleans, LA, USA) List(1011751, -4, MSY, SFO) List(SFO, San Francisco, CA, USA) List(1021507, 536, SFO, JFK) List(JFK, New York, NY, USA) List(MSY, New Orleans, LA, USA) List(2121725, 15, MSY, SFO) List(SFO, San Francisco, CA, USA) List(2131420, 504, SFO, SAN) List(SAN, San Diego, CA, USA) List(MSY, New Orleans, LA, USA) List(2091725, 87, MSY, SFO) List(SFO, San Francisco, CA, USA) List(2092110, 740, SFO, MIA) List(MIA, Miami, FL, USA) List(MSY, New Orleans, LA, USA) List(2091725, 87, MSY, SFO) List(SFO, San Francisco, CA, USA) List(2092230, 636, SFO, JFK) List(JFK, New York, NY, USA) List(SNA, Orange County, CA, USA) List(2190755, -7, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2190925, 1638, SFO, ORD) List(ORD, Chicago, IL, USA) List(SNA, Orange County, CA, USA) List(2182030, 12, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2190925, 1638, SFO, ORD) List(ORD, Chicago, IL, USA) List(SNA, Orange County, CA, USA) List(2181935, 9, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2190925, 1638, SFO, ORD) List(ORD, Chicago, IL, USA) List(SNA, Orange County, CA, USA) List(2180940, 8, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2190925, 1638, SFO, ORD) List(ORD, Chicago, IL, USA) List(SNA, Orange County, CA, USA) List(2181320, 12, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2190925, 1638, SFO, ORD) List(ORD, Chicago, IL, USA) List(SNA, Orange County, CA, USA) List(2181630, 14, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2190925, 1638, SFO, ORD) List(ORD, Chicago, IL, USA) List(SNA, Orange County, CA, USA) List(2130755, 10, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2131420, 504, SFO, SAN) List(SAN, San Diego, CA, USA) List(SNA, Orange County, CA, USA) List(2130940, 230, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2131420, 504, SFO, SAN) List(SAN, San Diego, CA, USA) List(SNA, Orange County, CA, USA) List(2131320, 94, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2131420, 504, SFO, SAN) List(SAN, San Diego, CA, USA) List(SNA, Orange County, CA, USA) List(2121825, 0, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2131420, 504, SFO, SAN) List(SAN, San Diego, CA, USA) List(SNA, Orange County, CA, USA) List(2121650, 6, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2131420, 504, SFO, SAN) List(SAN, San Diego, CA, USA) List(SNA, Orange County, CA, USA) List(2122025, 14, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2131420, 504, SFO, SAN) List(SAN, San Diego, CA, USA) List(SNA, Orange County, CA, USA) List(2091825, 139, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092110, 740, SFO, MIA) List(MIA, Miami, FL, USA) List(SNA, Orange County, CA, USA) List(2091825, 139, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092230, 636, SFO, JFK) List(JFK, New York, NY, USA) List(SNA, Orange County, CA, USA) List(2091650, 79, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092110, 740, SFO, MIA) List(MIA, Miami, FL, USA) List(SNA, Orange County, CA, USA) List(2091650, 79, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092230, 636, SFO, JFK) List(JFK, New York, NY, USA) List(SNA, Orange County, CA, USA) List(2091105, 39, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092110, 740, SFO, MIA) List(MIA, Miami, FL, USA) List(SNA, Orange County, CA, USA) List(2091105, 39, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092230, 636, SFO, JFK) List(JFK, New York, NY, USA) List(SNA, Orange County, CA, USA) List(2091335, 145, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092110, 740, SFO, MIA) List(MIA, Miami, FL, USA) List(SNA, Orange County, CA, USA) List(2091335, 145, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092230, 636, SFO, JFK) List(JFK, New York, NY, USA) List(SNA, Orange County, CA, USA) List(2092025, 0, SNA, SFO) List(SFO, San Francisco, CA, USA) List(2092110, 740, SFO, MIA) List(MIA, Miami, FL, USA) List(S

In [0]:
ranks = tripGraph.pageRank(resetProbability=0.15, maxIter=5)

In [0]:
display(ranks.vertices.orderBy(desc("pagerank")).limit(20))

id City State Country pagerank ATL Atlanta GA USA 18.910104616729814 DFW Dallas TX USA 13.699227467378964 ORD Chicago IL USA 13.163049993795985 DEN Denver CO USA 9.723388283811563 LAX Los Angeles CA USA 8.703656827807166 IAH Houston TX USA 7.991324463091128 SFO San Francisco CA USA 6.903242998287933 PHX Phoenix AZ USA 6.505886984498643 SLC Salt Lake City UT USA 5.799587684561128 LAS Las Vegas NV USA 5.25359244560915 SEA Seattle WA USA 4.626877547905697 EWR Newark NJ USA 4.401221169028188 MCO Orlando FL USA 4.389045874474043 CLT Charlotte NC USA 4.378459524081744 DTW Detroit MI USA 4.223377976049847 MSP Minneapolis MN USA 4.1490048912541795 LGA New York NY USA 4.129454491295321 BOS Boston MA USA 3.812077076528526 BWI Baltimore MD USA 3.53116352570383 JFK New York NY USA 3.521942669296845